![](https://images.elo7.com.br/assets/v3/desktop/svg/logo-elo7.svg)

### Teste prático Elo7: Avaliação de Ranking

Nesse notebook buscamos avaliar a qualidade dos rankings gerados a partir das consultas disponíveis no dataset do teste. 

Segundo a descrição do *dataset*, cada registro corresponde a um clique em um produto a partir de um termo de busca. Desse modo, só temos acesso a julgamentos de relevância positivos. Por consequência, o *dataset* não nos oferece acesso à coleção completa. Isso limita drasticamente a possibilidade de computar métricas representativas "tradicionais" da área de *Information Retrieval* (IR).

Considerando a situação descrita, optamos por utilizar a métrica *Mean Reciprocal Rank* (MRR), que leva em consideração apenas a posição do documento relevante. O MRR é definido por:

$$MRR = \frac{1}{|Q|} \sum_{i=1}^{|Q|} \frac{1}{rank_i}$$

Onde \\(Q\\) é o conjunto das consultas para avaliação e \\(rank_i\\) é a posição do primeiro produto relevante para a \\(i\\)-ésima consulta. No nosso caso, desconsideramos o fato do produto ser o primeiro relevante devido à falta de informações adicionais.

Com o MRR, podemos obter um valor quantitativo e comparar a qualidade de *rankings* em nossa coleção. Podemos também computar o MRR para as posições listadas no *dataset*, mas deve-se ter em mente que esses valores não são diretamente comparáveis com nossos *rankings*, pois supõe-se que a posição do *dataset* leva em consideração a coleção inteira, o que torna a tarefa bem mais difícil.

Para nossa avaliação, faremos uso das classes implementadas no módulo `search.py`, correspondentes à Parte 1 do teste.

In [1]:
import pandas as pd
import numpy as np
import search

path = 'elo7_recruitment_dataset.csv'

def mrr(position_list):
    return np.mean(np.divide(1., position_list, out=np.zeros_like(position_list), where=position_list!=0))

def query_then_mrr(df, search_engine):
    ranking_position_list = []

    for row in df_elo7.itertuples():
        try:
            ranking = list(zip(*search_engine.process_query(row.query)))[0]
            rank_pos = ranking.index(str(row.product_id))
            ranking_position_list.append(rank_pos)
        except:
            ranking_position_list.append(0)
            
    return mrr(np.asarray(ranking_position_list, dtype=float))

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Filipe\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package rslp to
[nltk_data]     C:\Users\Filipe\AppData\Roaming\nltk_data...
[nltk_data]   Package rslp is already up-to-date!


Primeiro, carregamos o dataset e suas posições de *ranking* correspondentes, bem como nossa `text-based search engine`.

In [2]:
# Load dataset
df_elo7 = pd.read_csv(path, sep=',', encoding='utf-8', header=0)

# Dataset's positions
# Account for search_page and adjust 0-indexed positions
baseline_position_list = (df_elo7['position'] + 38 * (df_elo7['search_page'] - 1)) + 1 

# Inverted Index creation/loading
inverted_index = search.InvertedIndex(path)

# Saving index for posterior use
# inverted_index.save_index()

# Ranker instantiation
ranker = search.BM25Ranker()
search_engine = search.Search(inverted_index, ranker)

Para fins de análise, vamos avaliar a performance do nosso *ranking* de modo global e também fazendo uma análise *breakdown* por cada uma das 5 categorias disponíveis.

In [3]:

# Querying

ranking_position_list = []

for row in df_elo7.itertuples():
    try:
        ranking = list(zip(*search_engine.process_query(row.query)))[0]
        rank_pos = ranking.index(str(row.product_id))
        ranking_position_list.append(rank_pos)
    except:
        ranking_position_list.append(0)
#         print(row.query, row.product_id, row.title, row.position)
# query_results = df_elo7['query'].apply(search_engine.process_query)

Loading index...
Could not load index.
Building index...
Done!


In [17]:
ranking_mrr = mrr(np.asarray(ranking_position_list, dtype=float))

0.14895329047068737


In [4]:
mrr(np.asarray(ranking_position_list, dtype=float))

0.1443832261189137

In [6]:
inverted_index.dictionary

defaultdict(list,
            {'mandal': [['11394449', 2],
              ['5928748', 2],
              ['7956533', 2],
              ['12661368', 1],
              ['7641901', 1],
              ['8038106', 3],
              ['5043690', 2],
              ['5081634', 2],
              ['1710707', 2],
              ['11560795', 2],
              ['6606774', 2],
              ['15297311', 1],
              ['5848047', 1],
              ['9480342', 3],
              ['1696803', 1],
              ['11666171', 2],
              ['486493', 3],
              ['9954611', 2],
              ['5102421', 1],
              ['4947299', 2],
              ['2759339', 2],
              ['3768791', 2],
              ['10798100', 1],
              ['11460425', 1],
              ['13664132', 3],
              ['15281989', 1],
              ['1432151', 2],
              ['442576', 1],
              ['5795180', 2],
              ['1001814', 1],
              ['8833023', 1],
              ['16656011', 2],
    

In [14]:
df_elo7

product_id  seller_id                                    query  \
0        11394449    8324141                           espirito santo   
1        15534262    6939286                         cartao de visita   
2        16153119    9835835                    expositor de esmaltes   
3        15877252    8071206      medidas lencol para berco americano   
4        15917108    7200773                     adesivo box banheiro   
...           ...        ...                                      ...   
38502    16561714    9813770                 nossa senhora de perolas   
38503    12716324    6483096  lembrancinha personalizada dia dos pais   
38504      972256    4840665                          copo metalizado   
38505     7291315    6420917                   festa do pijama menino   
38506    15908997    8784924                       festa tema musical   

       search_page  position                                           title  \
0                2         6                          Mandala Espírito Santo   
1                2         0                                Cartão de Visita   
2                1        38            Organizador expositor p/ 70 esmaltes   
3                1         6                  Jogo de Lençol Berço Estampado   
4                3        38                         ADESIVO BOX DE BANHEIRO   
...            ...       ...                                             ...   
38502            1         7  Imagem Nossa Senhora Aparecida em Perolas 25cm   
38503            1        27                     LEMBRANCINHA - DIA DOS PAIS   
38504            1         3                        Copos Metalizados - Rosé   
38505            1        36                     Kit Festa do Pijama Meninos   
38506            1         6              Mini Baleiro Instrumentos Musicais   

                                       concatenated_tags        creation_date  \
0                                            mandala mdf  2015-11-14 19:42:12   
1      cartao visita panfletos tag adesivos copos lon...  2018-04-04 20:55:07   
2                                              expositor  2018-10-13 20:57:07   
3                      t jogo lencol menino lencol berco  2017-02-27 13:26:03   
4                                   adesivo box banheiro  2017-05-09 13:18:38   
...                                                  ...                  ...   
38502                     senhora aparecida bebe perolas  2018-04-02 19:43:07   
38503                                      lembrancinhas  2018-07-10 11:41:08   
38504  despedida bianca metalizados xvdakaw lembranci...  2018-02-17 15:53:23   
38505                                       festa pijama  2016-08-21 22:33:59   
38506     tema musica instrumentos musicais festa musica  2018-07-16 02:42:46   

            price  weight  express_delivery  minimum_quantity  view_counts  \
0      171.890000  1200.0                 1                 4          244   
1       77.670000     8.0                 1                 5          124   
2       73.920006  2709.0                 1                 1           59   
3      118.770004     0.0                 1                 1          180   
4      191.810000   507.0                 1                 6           34   
...           ...     ...               ...               ...          ...   
38502   71.200000   706.0                 1                 4          315   
38503   14.650000     7.0                 1                26         1288   
38504   11.580000    25.0                 1               104          306   
38505  131.330000     0.0                 1                11           55   
38506    3.200000     8.0                 1                10          185   

       order_counts       category  
0               NaN      Decoração  
1               NaN    Papel e Cia  
2               NaN         Outros  
3               1.0           Bebê  
4               NaN      Decoração  
...             ...            ...  


In [7]:
df_elo7.loc[df_elo7['category'] == 'Outros']

product_id  seller_id                          query  search_page  \
2        16153119    9835835          expositor de esmaltes            1   
34        6951810     794953        comedouro para passaros            1   
41       16441196    2347079            adesivo para roupas            1   
131       5090504    4062928  roupa de croche para cachorro            1   
149      13924152    3615163                         biombo            1   
...           ...        ...                            ...          ...   
38368    16080632     716265                       cama pet            1   
38402    15773817    2056652                         pompom            1   
38426     4335246    3230602           camiseta pai e filha            2   
38441     6026509    4303271           lembrancinha aquario            1   
38485     6068009    8127708              sabonete decorado            1   

       position                                              title  \
2            38               Organizador expositor p/ 70 esmaltes   
34           28             Comedouro Especial Para Pássaros Apple   
41            4           tachinhas para roupas, customização 50un   
131           0                         Roupa de lã para seu Pet P   
149          17                                  Biombo - Florinda   
...         ...                                                ...   
38368        16                                         Cama Pet G   
38402         4  Pompom Pacote 20 Unidades Pompom 30 Mm 3 Cm Ar...   
38426        32                           Kit Camiseta Pai e filha   
38441        15                                 Aquário de Garrafa   
38485        30                        Sabonete Decorado ramalhete   

                                       concatenated_tags        creation_date  \
2                                              expositor  2018-10-13 20:57:07   
34        casas passarinho comedouros comedouro passaros  2015-01-20 22:19:45   
41     ilhos tachinhas rebites spikes customizacao tu...  2016-07-07 15:21:09   
131                            roupas cachorros roupinha  2017-05-31 18:06:34   
149                                              biombos  2013-03-09 21:58:05   
...                                                  ...                  ...   
38368                                       camas whisky  2017-05-29 18:19:35   
38402    lacos arcos mf pompom pompons ninhos atividades  2018-06-29 12:42:58   
38426                             kit pai dia pais papai  2017-09-06 02:45:56   
38441                                            aquario  2019-03-28 20:24:41   
38485  batizado sabonete dia maes nascimento casament...  2012-09-15 23:44:00   

            price  weight  express_delivery  minimum_quantity  view_counts  \
2       73.920006  2709.0                 1                 1           59   
34     101.770000   435.0                 0                 4           78   
41      17.450000    55.0                 1                 0          297   
131     41.310000   107.0                 1                 1          998   
149    464.000000  9008.0                 1                 5          114   
...           ...     ...               ...               ...          ...   
38368  229.400000     6.0                 1                 1          107   
38402   26.529999     8.0                 0                 0         1909   
38426   78.950005     6.0                 1                 1          113   
38441   31.650000   667.0                 0                 0           47   
38485    4.900000   109.0                 0                 5           78   

       order_counts category  
2               NaN   Outros  
34             21.0   Outros  
41              9.0   Outros  
131             8.0   Outros  
149             NaN   Outros  
...             ...      ...  
38368          13.0   Outros  
38402          82.0   Outros  
38426          14.0   Outros  
38441          17.0   Outros  
38

In [14]:
mrr(baseline_position_list)

0.11513195083037255

In [3]:
a = np.array([3, 1, 2])
mrr(a)

0.611111111111111

In [ ]:
\\\\||  \\(Q\\)

In [ ]:
MRRRRRRR BREAKDOWN ANALYSIS